# Trading Using Moving Average

## IMPORT DATASETS AND LIBRARIES

In [ ]:
# Mount the drive
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import seaborn as sns
from copy import copy
from scipy import stats
import plotly.express as px
import plotly.figure_factory as ff
import plotly.graph_objects as go

In [ ]:
# Ignore harmless warnings
import warnings
warnings.filterwarnings("ignore")

In [ ]:
from tqdm.notebook import tqdm

In [ ]:
# Read the stock data csv file, here's the list of the stocks considered:

# AAPL = Apple Stock 
# BA = Boeing 
# T = AT&T
# MGM = MGM Resorts International (Hotel Industry)
# AMZN = Amazon
# IBM = IBM
# TSLA = Tesla Motors
# GOOG = Google 
# sp500 = US Stock Market (S&P 500 is a stock market index that measures the stock performance of 500 large companies listed on U.S. stock exchange)
# Check the list of S&P 500 companies here: https://en.wikipedia.org/wiki/List_of_S%26P_500_companies

stocks_df = pd.read_csv('/content/drive/MyDrive/my files/Financial Analysis/stock.csv')
stocks_df

Date        AAPL          BA  ...         TSLA         GOOG        sp500
0     2012-01-12   60.198570   75.510002  ...    28.250000   313.644379  1295.500000
1     2012-01-13   59.972858   74.599998  ...    22.790001   311.328064  1289.089966
2     2012-01-17   60.671429   75.239998  ...    26.600000   313.116364  1293.670044
3     2012-01-18   61.301430   75.059998  ...    26.809999   315.273285  1308.040039
4     2012-01-19   61.107143   75.559998  ...    26.760000   318.590851  1314.500000
...          ...         ...         ...  ...          ...          ...          ...
2154  2020-08-05  440.250000  174.279999  ...  1485.020020  1473.609985  3327.770020
2155  2020-08-06  455.609985  172.199997  ...  1489.579956  1500.099976  3349.159912
2156  2020-08-07  444.450012  170.020004  ...  1452.709961  1494.489990  3351.280029
2157  2020-08-10  450.910004  179.410004  ...  1418.569946  1496.099976  3360.469971
2158  2020-08-11  437.500000  180.130005  ...  1374.390015  1480.319946  3333.689941

[2159 rows x 10 columns]

In [ ]:
# Sort the stock data by date
stocks_df = stocks_df.sort_values(by = ['Date'])
stocks_df

Date        AAPL          BA  ...         TSLA         GOOG        sp500
0     2012-01-12   60.198570   75.510002  ...    28.250000   313.644379  1295.500000
1     2012-01-13   59.972858   74.599998  ...    22.790001   311.328064  1289.089966
2     2012-01-17   60.671429   75.239998  ...    26.600000   313.116364  1293.670044
3     2012-01-18   61.301430   75.059998  ...    26.809999   315.273285  1308.040039
4     2012-01-19   61.107143   75.559998  ...    26.760000   318.590851  1314.500000
...          ...         ...         ...  ...          ...          ...          ...
2154  2020-08-05  440.250000  174.279999  ...  1485.020020  1473.609985  3327.770020
2155  2020-08-06  455.609985  172.199997  ...  1489.579956  1500.099976  3349.159912
2156  2020-08-07  444.450012  170.020004  ...  1452.709961  1494.489990  3351.280029
2157  2020-08-10  450.910004  179.410004  ...  1418.569946  1496.099976  3360.469971
2158  2020-08-11  437.500000  180.130005  ...  1374.390015  1480.319946  3333.689941

[2159 rows x 10 columns]

In [ ]:
# Print out the number of stocks
print('Total Number of stocks : {}'.format(len(stocks_df.columns[1:])))

Total Number of stocks : 9


In [ ]:
# Print the name of stocks
print('Stocks under consideration are:')

for i in stocks_df.columns[1:]:
  print(i)

Stocks under consideration are:
AAPL
BA
T
MGM
AMZN
IBM
TSLA
GOOG
sp500


In [ ]:
stocks_df.describe()

AAPL           BA  ...         GOOG        sp500
count  2159.000000  2159.000000  ...  2159.000000  2159.000000
mean    140.819823   189.942700  ...   783.712512  2218.749554
std      70.827601   103.678586  ...   334.448057   537.321727
min      55.790001    67.239998  ...   278.481171  1278.040039
25%      89.165714   124.015000  ...   527.214416  1847.984985
50%     116.599998   142.419998  ...   737.599976  2106.629883
75%     175.019997   297.044998  ...  1079.744995  2705.810059
max     455.609985   440.619995  ...  1568.489990  3386.149902

[8 rows x 9 columns]

In [ ]:
# Check if data contains any null values
stocks_df.isnull().sum()

Date     0
AAPL     0
BA       0
T        0
MGM      0
AMZN     0
IBM      0
TSLA     0
GOOG     0
sp500    0
dtype: int64

In [ ]:
# Getting dataframe info
stocks_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2159 entries, 0 to 2158
Data columns (total 10 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   Date    2159 non-null   object 
 1   AAPL    2159 non-null   float64
 2   BA      2159 non-null   float64
 3   T       2159 non-null   float64
 4   MGM     2159 non-null   float64
 5   AMZN    2159 non-null   float64
 6   IBM     2159 non-null   float64
 7   TSLA    2159 non-null   float64
 8   GOOG    2159 non-null   float64
 9   sp500   2159 non-null   float64
dtypes: float64(9), object(1)
memory usage: 185.5+ KB


## CALCULATE AND VISUALIZE MOVING AVERAGE

In [ ]:
# visualize the original stock price data, you can select which stocks you are interested in by changing the df.columns index 
for i in stocks_df.columns[1:]:
  fig = px.line(x = stocks_df.Date, y = stocks_df[i], title = i + ' price')
  fig.show()

In [ ]:
# copy the original dataframe to a new dataframe
moving_average_df = copy(stocks_df)

In [ ]:
# Create a moving average with 21 days window
# This is done by creating a loop through each stock & calculate the average using rolling(21)
# Note that the first 20 days shows NaN since we do not have data available
for i in stocks_df.columns[1:]:
  moving_average_df[i] = stocks_df[i].rolling(21).mean()

# View the first 30 elements
moving_average_df.head(30)

Date       AAPL         BA  ...       TSLA        GOOG        sp500
0   2012-01-12        NaN        NaN  ...        NaN         NaN          NaN
1   2012-01-13        NaN        NaN  ...        NaN         NaN          NaN
2   2012-01-17        NaN        NaN  ...        NaN         NaN          NaN
3   2012-01-18        NaN        NaN  ...        NaN         NaN          NaN
4   2012-01-19        NaN        NaN  ...        NaN         NaN          NaN
5   2012-01-20        NaN        NaN  ...        NaN         NaN          NaN
6   2012-01-23        NaN        NaN  ...        NaN         NaN          NaN
7   2012-01-24        NaN        NaN  ...        NaN         NaN          NaN
8   2012-01-25        NaN        NaN  ...        NaN         NaN          NaN
9   2012-01-26        NaN        NaN  ...        NaN         NaN          NaN
10  2012-01-27        NaN        NaN  ...        NaN         NaN          NaN
11  2012-01-30        NaN        NaN  ...        NaN         NaN          NaN
12  2012-01-31        NaN        NaN  ...        NaN         NaN          NaN
13  2012-02-01        NaN        NaN  ...        NaN         NaN          NaN
14  2012-02-02        NaN        NaN  ...        NaN         NaN          NaN
15  2012-02-03        NaN        NaN  ...        NaN         NaN          NaN
16  2012-02-06        NaN        NaN  ...        NaN         NaN          NaN
17  2012-02-07        NaN        NaN  ...        NaN         NaN          NaN
18  2012-02-08        NaN        NaN  ...        NaN         NaN          NaN
19  2012-02-09        NaN        NaN  ...        NaN         NaN          NaN
20  2012-02-10  63.986394  75.251428  ...  28.898571  298.615240  1322.072864
21  2012-02-13  64.538844  75.219999  ...  29.052857  298.201553  1324.752389
22  2012-02-14  65.148707  75.265714  ...  29.547143  297.840288  1327.676676
23  2012-02-15  65.645102  75.264285  ...  29.880476  297.294240  1330.036673
24  2012-02-16  66.142381  75.274285  ...  30.231428  296.668254  1332.417626
25  2012-02-17  66.648299  75.264285  ...  30.622381  295.839693  1334.642863
26  2012-02-21  67.291496  75.273809  ...  30.998571  296.504107  1336.872861
27  2012-02-22  67.874013  75.299999  ...  31.353333  297.035924  1338.856672
28  2012-02-23  68.526939  75.323333  ...  31.691905  297.633208  1341.180955
29  2012-02-24  69.042245  75.334761  ...  31.967143  298.591758  1343.070475

[30 rows x 10 columns]

In [ ]:
# Create a moving average plot
for i in stocks_df.columns[1:]:
  fig = px.line(x = moving_average_df.Date[20:], y = moving_average_df[i][20:], title= i + ' 21-days moving average')
  fig.show()

In [ ]:
# Overlay the 21-days moving average plot on top of stock original prices (without any averaging)
for i in stocks_df.columns[1:]:  
  fig = px.line(x = stocks_df.Date[20:], y = stocks_df[i][20:], title =  i + ' Original Stock Price vs. 21-days Moving Average change')
  fig.add_scatter(x = moving_average_df.Date[20:], y = moving_average_df[i][20:], name = '21-days moving average')
  fig.show()

## GENERATE BUY/SELL SIGNALS USING MOVING AVERAGE

In [ ]:
# create a signal dataframe 
# copy the dataframe
signals_df = copy(stocks_df)

In [ ]:
# logic to create buy (1) and sell (-1) signal
# if price is above the moving average, we buy since the trend is up
# if the price is below the moving average, we sell since the trend is down
# The moving average is a technical stock analysis tool that works by smoothing out price data or noise due to random short-term price fluctuations.
# As you increase the averaging window (look back window), the curve tend to become more smoother

# Loop on rows starting from row 21
for i in range(21, len(stocks_df)):

  # Loop on Columns (stock names)
  for j in stocks_df.columns[1:]:
    
    # Compare original stock data with the average 
    if  stocks_df[j][i] > moving_average_df[j][i]:
      signals_df[j][i] = 1

    elif  stocks_df[j][i] < moving_average_df[j][i]:
      signals_df[j][i] = -1
    
    else:
      signals_df[j][i] = 0

In [ ]:
# Signal values (Buy/Sell decision table)
signals_df[21:]

Date  AAPL   BA    T  MGM  AMZN  IBM  TSLA  GOOG  sp500
21    2012-02-13   1.0 -1.0  1.0  1.0   1.0  1.0   1.0   1.0    1.0
22    2012-02-14   1.0  1.0  1.0  1.0   1.0  1.0   1.0   1.0    1.0
23    2012-02-15   1.0 -1.0 -1.0  1.0  -1.0  1.0   1.0   1.0    1.0
24    2012-02-16   1.0 -1.0  1.0  1.0  -1.0  1.0   1.0   1.0    1.0
25    2012-02-17   1.0  1.0  1.0  1.0  -1.0  1.0   1.0   1.0    1.0
...          ...   ...  ...  ...  ...   ...  ...   ...   ...    ...
2154  2020-08-05   1.0  1.0 -1.0  1.0   1.0  1.0  -1.0  -1.0    1.0
2155  2020-08-06   1.0 -1.0 -1.0  1.0   1.0  1.0  -1.0  -1.0    1.0
2156  2020-08-07   1.0 -1.0  1.0  1.0   1.0  1.0  -1.0  -1.0    1.0
2157  2020-08-10   1.0  1.0  1.0  1.0   1.0  1.0  -1.0  -1.0    1.0
2158  2020-08-11   1.0  1.0  1.0  1.0  -1.0  1.0  -1.0  -1.0    1.0

[2138 rows x 10 columns]

## EXECUTE A TRADE USING MOVING AVERAGE

In [ ]:
# Function to simulate a trade
# Note: We assume we started trading with $1M in assets
# Note: We don't want to spend more than 10% of the principal amount ($1M) on any specific stock so we restrict the buying amount to be 100,000.
# Note: We do not re-investing the profit to buy more stocks

def trade(signals_df):
  
  # create a dictionary to hold the number of stocks that we are buying
  buy = {}

  # list to store the profit/loss values over the trading time period
  profit_loss_change = []
  
  # list to store the dates in which profit/loss values were added to the list above
  date = []
  
  # Assign 0 to all stocks in the dictionary
  for i in stocks_df.columns[1:]:
    buy[i] = 0

  # Start with a principal amount of $1M
  amount = 1000000
  
  # placeholder to track profits & losses
  profit_loss_tracker = {'pl': 0}
  
  # loop through all rows in the dataframe 
  for i in range(len(stocks_df)-1):
    
    # for each index, we loop through the all available stocks to get the signal
    for j in stocks_df.columns[1:]:
      
      # BUY SIGNALS
      # if the signal is buy (1), we pass through this:
      if signals_df[j][i] == 1:
        
        # Since we don't want to spend more than 10% of the principal amount ($1M) on one specific stock,
        # we restrict the buying amount to be $100,000. 
        # Hence, we check if (1) we have funds over $99,999 and (2) don't own this specific stock at the moment (i.e.: buy[j] == 0)
        if amount > 99999 and buy[j] == 0:
          
          # Since signal is generated based on the closing stock price, we buy based on the next day price (df[j][i+1])
          # Let's calculate the number of stock units that we are buying
          # Number of stock units = Max funds(Balance)/next day price
          units = 100000/stocks_df[j][i+1]
          
          # Reduce the amount spent to buy the stock i.e.: $100,000 from the principal amount
          amount = amount - 100000

          # Add the number of units bought to the acquired stocks dictionary
          buy[j] = units

      # SELL SIGNALS  
      # Check the sell signal and also make sure we own the stock that we want to sell
      elif signals_df[j][i] == -1 and buy[j] > 0:
          
          # We sell the stock based on next day price and calculate the profit or loss
          change = (buy[j] * stocks_df[j][i+1]) - 100000
          
          # Change the number of units owned to 0 because we already sold them
          buy[j] = 0
          
          # We are not re-investing profit, we take out the profit and only add 100,000 to the
          # principal if we have profit, in case we incur loss we remove the loss from the principal
          amount = amount + min(100000, 100000 + change)
          
          # Add the profit/loss to the dictionary
          profit_loss_tracker['pl'] = profit_loss_tracker['pl'] + change
          
          # Append the p/l value to the list
          profit_loss_change.append(profit_loss_tracker['pl'])
          
          # Append the date to the list
          date.append(stocks_df['Date'][i])

  return profit_loss_change, date, buy


In [ ]:
# Call the trading function and pass the signals dataframe as an argument
profit_loss_change, trade_date, buy = trade(signals_df)

In [ ]:
# Plot the net Profit/Loss
fig = px.line(x = trade_date, y = profit_loss_change, title = 'p/l')
fig.show()

## TECHNICAL ANALYSIS WITH MOMENTUM

In [ ]:
# Copy the dataframe
df_change  = copy(stocks_df)

In [ ]:
# Loop through each stock
for i in stocks_df.columns[1:]:

  # Loop through each row belonging to the stock
  for j in range(1, len(stocks_df)):
    
    # Calculate the percentage of change from the previous day (note that we obtained the log change)
    df_change[i][j] = ((np.log(stocks_df[i][j])- np.log(stocks_df[i][j-1])))
  
  # set the value of first row to zero, as previous value is not available
  df_change[i][0] = 0

In [ ]:
df_change

Date      AAPL        BA  ...      TSLA      GOOG     sp500
0     2012-01-12  0.000000  0.000000  ...  0.000000  0.000000  0.000000
1     2012-01-13 -0.003757 -0.012125  ... -0.214772 -0.007413 -0.004960
2     2012-01-17  0.011581  0.008542  ...  0.154589  0.005728  0.003547
3     2012-01-18  0.010330 -0.002395  ...  0.007864  0.006865  0.011047
4     2012-01-19 -0.003174  0.006639  ... -0.001867  0.010468  0.004927
...          ...       ...       ...  ...       ...       ...       ...
2154  2020-08-05  0.003618  0.054294  ... -0.001332  0.005880  0.006409
2155  2020-08-06  0.034294 -0.012007  ...  0.003066  0.017817  0.006407
2156  2020-08-07 -0.024800 -0.012740  ... -0.025063 -0.003747  0.000633
2157  2020-08-10  0.014430  0.053758  ... -0.023781  0.001077  0.002738
2158  2020-08-11 -0.030191  0.004005  ... -0.031639 -0.010603 -0.008001

[2159 rows x 10 columns]

In [ ]:
# Statistical information
df_change.describe()

AAPL           BA  ...         GOOG        sp500
count  2159.000000  2159.000000  ...  2159.000000  2159.000000
mean      0.000919     0.000403  ...     0.000719     0.000438
std       0.017780     0.022699  ...     0.015789     0.010532
min      -0.137708    -0.272444  ...    -0.117667    -0.127652
25%      -0.006948    -0.007872  ...    -0.006157    -0.003191
50%       0.000811     0.000780  ...     0.000603     0.000593
75%       0.009969     0.009421  ...     0.008572     0.005007
max       0.113157     0.217677  ...     0.148872     0.089683

[8 rows x 9 columns]

In [ ]:
# plot the returns based on consecutive days

for i in stocks_df.columns[1:]:
  fig1 = px.line(x = df_change.Date, y = df_change[i], title = i + ' change')
  fig1.show()

In [ ]:
# Plot the original stock price, the 21-days moving average and the daily change 

for i in stocks_df.columns[1:]:
  # fig = make_subplots(rows=2, cols=1)
  fig = px.line(x = stocks_df.Date[20:], y = stocks_df[i][20:], title= i + ' average change')
  fig.add_scatter(x = moving_average_df.Date[20:], y = moving_average_df[i][20:], name='21 Day Moving Average')
  fig2 = px.line(x = df_change.Date[20:], y = df_change[i][20:], title= i + ' average change')
  fig.show() 
  fig2.show()


In [ ]:
# Signal to buy and sell, if the return moving average changes from 0 to +ve and price is above the moving average we buy. 
# If the return moving average is moving from 0.5 to less than that and price is less than the moving average we sell
# also when return moving average changes from +ve to -ve we sell
for i in range(25, len(stocks_df)):
  for j in stocks_df.columns[1:]:
    
    if df_change[j][i] > 0 and df_change[j][i-1] < 0 and stocks_df[j][i] > moving_average_df[j][i]:
      signals_df[j][i] = 1
    
    elif df_change[j][i-1] > 0.05 and df_change[j][i] < 0.05 and stocks_df[j][i] < moving_average_df[j][i]:
      signals_df[j][i] = -1
    
    elif df_change[j][i-1] > 0 and df_change[j][i] < 0:
      signals_df[j][i] = -1
    
    else:
      signals_df[j][i] = 0

In [ ]:
# Do the trade using the new signal table
pl_change, id, buy = trade(signals_df)

In [ ]:
fig = px.line(x = id, y = pl_change, title = 'p/l')
fig.show()

In [ ]:
a = pd.DataFrame({'return': pl_change})
a = a['return'].diff()
sharpe_ratio = a.mean()/a.std() * np.sqrt(252)
portfolio_return = np.sum(a.mean()) * 252 / 1000000
print("Annual rate of return : {}%".format(portfolio_return))
print("Sharpe ratio for the model is {}".format(sharpe_ratio))

Annual rate of return : 0.02901896833124455%
Sharpe ratio for the model is 0.7949383237930704
